In [3]:
from cmapPy.pandasGEXpress.parse_gct import parse
from cmapPy.pandasGEXpress.write_gct import write

import numpy as np
from scipy.stats import spearmanr
from statsmodels.stats.multitest import multipletests

In [24]:
data = parse('GTEx_Analysis_2017-06-05_v8_RNASeQCv1.1.9_gene_median_tpm.gct', ridx=[i for i in range(600)])
data.row_metadata_df.dropna(inplace=True)
data.data_df = data.data_df.loc[data.row_metadata_df.index]
dataset = data.data_df

print(len(dataset))

600


In [25]:
#To remove all entries for whom all values are 0, to prevent corr and p being NaN
for i in dataset.index.values:
    if np.sum(dataset.loc[i].values) == 0.0:
        dataset = dataset.drop(i, axis=0)
            
print(len(dataset))

510


In [10]:
individuals = dataset.index.values
bootstrapped_individuals = np.random.choice(individuals, len(individuals), replace=True)

NameError: name 'dataset' is not defined

In [27]:
p_values = []
corr_values = []

count = 0
for i in bootstrapped_individuals:
    for j in bootstrapped_individuals:
        
        count = count + 1
        if(count%10000 == 0):
            print(count)

        gene1 = dataset.loc[i].values
        gene2 = dataset.loc[j].values
        
        corr, p = spearmanr(gene1, gene2)
        
        corr_values.append(corr)
        p_values.append(p)

print(p_values)

10000
20000
30000
40000
50000
60000
70000
80000
90000
100000
110000
120000
130000
140000
150000
160000
170000
180000
190000
200000
210000
220000
230000
240000
250000
260000


IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [28]:
results = multipletests(p_values, alpha = 0.05, method='fdr_bh')
reject = results[0]
print(len(reject))
p_values_corrected = results[1]
results

260100


(array([ True,  True, False, ...,  True, False,  True]),
 array([0.00000000e+00, 0.00000000e+00, 4.35829803e-01, ...,
        2.31746676e-04, 9.61109548e-02, 0.00000000e+00]),
 1.9720603361417233e-07,
 1.922337562475971e-07)

In [29]:
#Making the Graph. It is a dictionary of the form {gene : [array of genes to which it has an edge]}
G = {}

for i in range(len(dataset)):
    temp = []
    for j in range(len(dataset)):
        if p_values_corrected[i*len(dataset) + j] > 0.1 and not reject[i*len(dataset) + j]:  #If its greater than cutoff and not rejected during multiple test correction
            temp.append(dataset.index[j])
            
    G.update({dataset.index[i] : temp})
    
G

{'ENSG00000223972.5': ['ENSG00000243485.5',
  'ENSG00000240361.1',
  'ENSG00000238009.6',
  'ENSG00000268903.1',
  'ENSG00000279928.2',
  'ENSG00000279457.4',
  'ENSG00000269732.1',
  'ENSG00000225972.1',
  'ENSG00000225630.1',
  'ENSG00000237973.1',
  'ENSG00000240409.1',
  'ENSG00000248527.1',
  'ENSG00000198744.5',
  'ENSG00000268663.1',
  'ENSG00000273547.1',
  'ENSG00000229376.3',
  'ENSG00000229905.1',
  'ENSG00000237491.8',
  'ENSG00000230092.7',
  'ENSG00000177757.2',
  'ENSG00000187583.10',
  'ENSG00000272512.1',
  'ENSG00000188290.10',
  'ENSG00000187608.8',
  'ENSG00000217801.9',
  'ENSG00000131591.17',
  'ENSG00000207607.3',
  'ENSG00000205231.1',
  'ENSG00000230415.1',
  'ENSG00000162572.20',
  'ENSG00000131584.18',
  'ENSG00000169972.11',
  'ENSG00000127054.20',
  'ENSG00000169962.4',
  'ENSG00000107404.19',
  'ENSG00000223663.2',
  'ENSG00000272455.1',
  'ENSG00000235098.8',
  'ENSG00000225905.1',
  'ENSG00000205116.3',
  'ENSG00000225285.1',
  'ENSG00000215915.9',
  'EN

In [30]:
import pickle
f = open("file2.pkl","wb")

pickle.dump(G,f)
f.close()
print("Graph saved")

Graph saved


In [31]:
len(G)

510